# Detect Outliers

In our EDA in R, we determined that the ids 524  692 1183 1299 (R counts start at 1!) had very large GrLivArea, while 31 496 534 917 969 had very low SalePrice for their size, relative to the rest of the population. We want to determine what sets of points can be dropped in order to increase prediction accuracy on a validation set.

In [6]:
# we decrement by 1 in order to conform with python counting
pot_outliers = [524-1, 692-1, 1183-1, 1299-1, 31-1, 496-1, 534-1, 917-1, 969-1]

In [21]:
import itertools
import numpy as np
import pandas as pd
pd.set_option('display.precision',20)

from sklearn import linear_model
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import cross_val_predict, KFold, cross_val_score, GridSearchCV, \
                                    ShuffleSplit

In [2]:
# def to compare goodness of fit on training set
def rmse(y_true, y_pred):
    return np.sqrt(mean_squared_error(y_true, y_pred))

We import the preprocessed data set that includes all data points.

In [4]:
df = pd.read_csv("input/train_tidy_000000000.csv")

The columns GarageAge and GarageAgeLin have NAs. We have to drop them unless we drop the rows with NoGarage == 1 instead. For now, we just drop GarageAge and GarageAgeLin.

In [15]:
df.drop(['GarageAge', 'GarageAgeLin'], axis=1, inplace=True)

We want to split this into a training and validation set. We want the potential outliers to be in the training set.

In [18]:
outlier_df = df.iloc[pot_outliers]

In [19]:
nooutlier_df = df.drop(pot_outliers)

In [22]:
ss = ShuffleSplit(n_splits=1, test_size=0.20, random_state=89)

In [23]:
X = nooutlier_df.values

In [25]:
for train_idx, validation_idx in ss.split(X):
    train_df = nooutlier_df.iloc[train_idx]
    validation_df = nooutlier_df.iloc[validation_idx]

In [29]:
train_df = train_df.append(outlier_df)

We'll set up the matrices we use for the validation set, since these won't change as we drop outliers. 

In [31]:
y_validation = validation_df['SalePrice'].values
x_validation = validation_df.drop(['HouseId', 'SalePrice'],axis=1).values

We will use the LassoLarsCV model and RMS error as our metric.  This is because, as we will see, linear models do reasonably well on this problem and the regularization hyperparameter is automatically selected by CV on the training data.

In [32]:
# Cross-validation sets
kfold = KFold(n_splits=10, random_state=7)

lr = linear_model.LassoLarsCV(verbose=False, max_iter=5000,precompute='auto', cv=kfold, max_n_alphas=1000, n_jobs=-1)

We want to set a baseline value by training on the full dataset and then predicting on the validation set.

In [33]:
y_train = train_df['SalePrice'].values
x_train = train_df.drop(['HouseId', 'SalePrice'],axis=1).values
lr.fit(x_train, y_train)
y_pred = lr.predict(x_validation)

/usr/lib64/python2.7/site-packages/sklearn/linear_model/least_angle.py:309: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 211 iterations, i.e. alpha=3.547e-05, with an active set of 173 regressors, and the smallest cholesky pivot element being 2.220e-16
  ConvergenceWarning)
/usr/lib64/python2.7/site-packages/sklearn/linear_model/least_angle.py:309: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 263 iterations, i.e. alpha=2.060e-05, with an active set of 207 regressors, and the smallest cholesky pivot element being 2.107e-08
  ConvergenceWarning)
/usr/lib64/python2.7/site-packages/sklearn/linear_model/least_angle.py:309: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 269 iterations, i.e. alpha=1.923e-05, with an active set of 209 regressors, and the smallest cholesky pivot element being 1.490e-08
  ConvergenceWarning)
/usr/lib64/python2.7/site-packages/sklearn/linear_model

NameError: name 'x_pred' is not defined

In [35]:
baseline = rmse(y_validation, y_pred)
baseline

0.12503266782864195

We'll examine dropping all possible sets of outliers.  There are 512 total combinations including the baseline where we don't drop any points. train_df is still indexed by HouseId - 1

In [55]:
comb_drop_results_df = pd.DataFrame(dtype = 'float64')
count = 0 
for L in range(0, len(pot_outliers)+1):
        for subset in itertools.combinations(pot_outliers, L):
            drop_pts = list(subset)
            comb_drop_results_df.loc[count, 'Dropped'] = str([x+1 for x in drop_pts])
            y_train = train_df['SalePrice'].drop(drop_pts).values
            x_train = train_df.drop(['HouseId', 'SalePrice'],axis=1).drop(drop_pts).values
            lr.fit(x_train, y_train)
            y_pred = lr.predict(x_validation)
            error = rmse(y_validation, y_pred)
            comb_drop_results_df.loc[count, 'RMSE'] = error
            comb_drop_results_df.loc[count, 'Diff from Base'] = error - baseline
            count += 1

/usr/lib64/python2.7/site-packages/sklearn/linear_model/least_angle.py:309: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 211 iterations, i.e. alpha=3.547e-05, with an active set of 173 regressors, and the smallest cholesky pivot element being 2.220e-16
  ConvergenceWarning)
/usr/lib64/python2.7/site-packages/sklearn/linear_model/least_angle.py:309: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 236 iterations, i.e. alpha=2.616e-05, with an active set of 192 regressors, and the smallest cholesky pivot element being 1.490e-08
  ConvergenceWarning)
/usr/lib64/python2.7/site-packages/sklearn/linear_model/least_angle.py:309: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 263 iterations, i.e. alpha=2.060e-05, with an active set of 207 regressors, and the smallest cholesky pivot element being 2.107e-08
  ConvergenceWarning)
/usr/lib64/python2.7/site-packages/sklearn/linear_model

In [56]:
comb_drop_results_df.sort_values(['RMSE'])

Dropped                    RMSE  \
312                       [524, 1299, 31, 496, 917]  0.11751015503521701488   
418                 [524, 1183, 1299, 31, 496, 917]  0.11767344602977361512   
403                  [524, 692, 1299, 31, 496, 917]  0.11767832787658395743   
487            [524, 1183, 1299, 31, 496, 534, 917]  0.11794212227929237735   
509       [524, 1183, 1299, 31, 496, 534, 917, 969]  0.11794722296893855873   
489            [524, 1183, 1299, 31, 496, 917, 969]  0.11800623920290025104   
432                  [524, 1299, 31, 496, 534, 917]  0.11801314170909987800   
481             [524, 692, 1299, 31, 496, 534, 917]  0.11807551789471042170   
434                  [524, 1299, 31, 496, 917, 969]  0.11808353826327439018   
493             [524, 1299, 31, 496, 534, 917, 969]  0.11808925058320160484   
469            [524, 692, 1183, 1299, 31, 534, 917]  0.11809304315437758881   
293                      [524, 1183, 1299, 31, 917]  0.11811145238852943651   
502       [524, 692, 1183, 1299, 31, 496, 534, 917]  0.11812073829008722103   
384                 [524, 692, 1183, 1299, 31, 917]  0.11814180245061871311   
420                 [524, 1183, 1299, 31, 534, 917]  0.11816002695518822152   
291                      [524, 1183, 1299, 31, 496]  0.11818539202502657826   
314                       [524, 1299, 31, 534, 917]  0.11823093780475249504   
511  [524, 692, 1183, 1299, 31, 496, 534, 917, 969]  0.11825875839087966745   
273                       [524, 692, 1299, 31, 917]  0.11826306717438717087   
168                            [524, 1299, 31, 917]  0.11828484577193275340   
471            [524, 692, 1183, 1299, 31, 917, 969]  0.11829240029233729914   
508        [524, 692, 1299, 31, 496, 534, 917, 969]  0.11834604972103339449   
417                 [524, 1183, 1299, 31, 496, 534]  0.11836318181728958110   
166                            [524, 1299, 31, 496]  0.11836872540893240979   
151                           [524, 1183, 1299, 31]  0.11844049998913100397   
256                      [524, 692, 1183, 1299, 31]  0.11844623825943885465   
383                 [524, 692, 1183, 1299, 31, 534]  0.11845422307020071762   
382                 [524, 692, 1183, 1299, 31, 496]  0.11846126214002140886   
292                      [524, 1183, 1299, 31, 534]  0.11846770193919965719   
405                  [524, 692, 1299, 31, 534, 917]  0.11852335526975571467   
..                                              ...                     ...   
192                            [692, 1183, 31, 534]  0.12573909067083716140   
107                                [1183, 534, 917]  0.12577937550170387171   
234                            [1183, 31, 534, 917]  0.12579587669816655326   
45                                       [917, 969]  0.12580433828236095573   
29                                      [1183, 917]  0.12581207385684270439   
450                  [692, 1183, 31, 496, 917, 969]  0.12582244282529592150   
499             [692, 1183, 31, 496, 534, 917, 969]  0.12585532296782037109   
128                                 [496, 917, 969]  0.12588989475390749417   
342                      [692, 1183, 496, 534, 917]  0.12593123047149623606   
78                                 [692, 1183, 917]  0.12595709055676149180   
231                            [1183, 31, 496, 534]  0.12598035884673494667   
105                                [1183, 496, 917]  0.12601612854747784587   
198                           [692, 1183, 534, 917]  0.12606035873127460767   
371                       [1183, 31, 496, 534, 917]  0.12621252896006013300   
251                             [31, 496, 534, 917]  0.12630338128576201751   
100                                 [1183, 31, 496]  0.12636138951105019279   
452                 [692, 1183, 496, 534, 917, 969]  0.12650186128973547883   
239                           [1183, 496, 917, 969]  0.12655239600601309036   
339                       [692, 1183, 31, 534, 917]  0.12664443701152089394   
27             

In [57]:
comb_drop_results_df.sort_values(['RMSE']).to_csv('comb_drop_results.csv', header=True)

We note that the difference from the baseline for all of these sets is very small, while the difference between sets is generally even smaller.  The (31, 496, 524, 917, 1299) set seems to be optimal, though the other top sets could be used to generate an ensemble of models.